In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
from sklearn import preprocessing
import mysql.connector
from pandas import DataFrame
from sklearn.metrics import jaccard_score
from numpy import logical_and as l_and, logical_not as l_not

In [6]:
disnet_db_ares = mysql.connector.connect(
  host="138.4.130.153",
  port = "30602",
  user="disnet_user",
  password="tYkX4JxV8p79",
  database="disnet_drugslayer"
)

 

disnet_mysql_cursor = disnet_db_ares.cursor()

In [14]:
def get_dummies(data,col_index,col_col):
    
    df_final= pd.get_dummies(data.set_index(col_index),col_col).reset_index()
    df_final=df_final.drop_duplicates()
    df_final=df_final.groupby(col_index).sum().reset_index()
    
    return df_final

def convert(lista):
    return tuple(i for i in lista)


def get_normal_diseases(rare_disease):
    '''
    Esta funcion devuelve un dataframe con la enfermedad, los medicamentos y los targets que son utiles
    para la enfermedad rara que se le pase como parametro'''
    
    
    q= f'''SELECT DISTINCT
        d.disease_id, drug_name,dg.gene_id
        FROM
        disnet_biolayer.disease_variant dv
            JOIN disnet_biolayer.disease d on dv.disease_id = d.disease_id
            JOIN disnet_biolayer.variant v on v.variant_id = dv.variant_id
            JOIN disnet_biolayer.disease_gene dg ON d.disease_id = dg.disease_id
            JOIN disnet_biolayer.encodes e ON dg.gene_id = e.gene_id
            JOIN disnet_drugslayer.has_code hc ON hc.code = e.protein_id
            JOIN disnet_drugslayer.drug_target dt ON hc.id = dt.target_id
            JOIN disnet_drugslayer.drug d ON dt.drug_id = d.drug_id
        WHERE
             hc.entity_id = 3
             and v.chromosome is not null
        and d.ddf_type = "disease"
        AND dg.gene_id in (SELECT distinct(gene_id) FROM disnet_biolayer.disease_gene
        where disease_id = "{rare_disease}")
        ;'''
    
    df = pd.read_sql(q, con=disnet_db_ares)
    
    return df

In [4]:
rare_diseases= ['C0011195', 'C0023944', 'C0024054', 'C0024901', 'C0027877', 'C0036391', 'C0265202', 'C0268059', 'C0549463', 'C0751337', 'C0869083', 'C1852146', 'C0796280']

matrix_jac_gen = pd.read_excel(("mat_jacc_variant.xlsx"),engine='openpyxl')
matrix_jac_gen

rare_dis_id  C0000744  C0000846  C0000889  C0001080  C0001127  C0001193  \
0    C0011195         0         0         0         0         0         0   
1    C0027877         0         0         0         0         0         0   
2    C0036391         0         0         0         0         0         0   
3    C0549463         0         0         0         0         0         0   
4    C0751337         0         0         0         0         0         0   
5    C1852146         0         0         0         0         0         0   

   C0001206  C0001311  C0001339  ...  C4540135  C4540251  C4540293  C4540389  \
0         0         0         0  ...         0         0         0         0   
1         0         0         0  ...         0         0         0         0   
2         0         0         0  ...         0         0         0         0   
3         0         0         0  ...         0         0         0         0   
4         0         0         0  ...         0         0         0         0   
5         0         0         0  ...         0         0         0         0   

   C4540439  C4540496  C4540534  C4540536  C4540602  C4543822  
0         0         0         0         0         0         0  
1         0         0         0         0         0         0  
2         0         0         0         0         0         0  
3         0         0         0         0         0         0  
4         0         0         0         0         0         0  
5         0         0         0         0         0         0  

[6 rows x 6953 columns]

In [85]:
df_useful_diseases = get_normal_diseases("C1852146")
df_useful_diseases

Empty DataFrame
Columns: [disease_id, drug_name, gene_id]
Index: []

In [66]:
useful_diseases = get_normal_diseases("C1852146")['disease_id'].drop_duplicates().tolist()
len(useful_diseases)

358

In [67]:
df = matrix_jac_gen[matrix_jac_gen.rare_dis_id == 'C1852146']
df.head(2)

rare_dis_id  C0000744  C0000846  C0000889  C0001080  C0001127  C0001193  \
3    C0549463         0         0         0         0         0         0   

   C0001206  C0001311  C0001339  ...  C4540135  C4540251  C4540293  C4540389  \
3         0         0         0  ...         0         0         0         0   

   C4540439  C4540496  C4540534  C4540536  C4540602  C4543822  
3         0         0         0         0         0         0  

[1 rows x 6953 columns]

In [68]:
df_useful = df[['rare_dis_id'] + useful_diseases].set_index('rare_dis_id').transpose()
df_useful.sort_values(by='C1852146', ascending=False)

rare_dis_id  C0549463
C0549463          1.0
C0002871          0.0
C0149925          0.0
C0085786          0.0
C0085435          0.0
...               ...
C0812413          0.0
C0751781          0.0
C0740457          0.0
C0699885          0.0
C4082937          0.0

[358 rows x 1 columns]

In [70]:
df_normal_dis_jacc=pd.DataFrame(df_useful['C1852146'].nlargest(5)).reset_index().rename(columns={'index':'disease_id', 'C1852146':'jacc_idx'})

In [71]:
df_normal_dis_jacc.to_excel("dis_jacc_C1852146_v.xlsx")

In [72]:
df_normal_rare_drug=pd.merge(df_useful_diseases,df_normal_dis_jacc,on="disease_id",how="inner")

In [73]:
df_normal_rare_drug

disease_id                drug_name  gene_id  jacc_idx
0    C0002871           MERCAPTOPURINE     3251       0.0
1    C0002871  PAZOPANIB HYDROCHLORIDE     3702       0.0
2    C0002871             FOSTAMATINIB     3702       0.0
3    C0002871                PAZOPANIB     3702       0.0
4    C0002871              DEQUALINIUM      331       0.0
5    C0002871               EMAPALUMAB     3458       0.0
6    C0002871               OLSALAZINE     3458       0.0
7    C0002871              GLUCOSAMINE     3458       0.0
8    C0003868           MERCAPTOPURINE     3251       0.0
9    C0004135           MERCAPTOPURINE     3251       0.0
10   C0006142           MERCAPTOPURINE     3251       0.0
11   C0006142  PAZOPANIB HYDROCHLORIDE     3702       0.0
12   C0006142             FOSTAMATINIB     3702       0.0
13   C0006142                PAZOPANIB     3702       0.0
14   C0006142             ZINC ACETATE      325       0.0
15   C0006142              DEQUALINIUM      331       0.0
16   C0006142               EMAPALUMAB     3458       0.0
17   C0006142               OLSALAZINE     3458       0.0
18   C0006142              GLUCOSAMINE     3458       0.0
19   C0006142               IXEKIZUMAB     3605       0.0
20   C0006142              SECUKINUMAB     3605       0.0
21   C0549463           MERCAPTOPURINE     3251       1.0
22   C0549463  PAZOPANIB HYDROCHLORIDE     3702       1.0
23   C0549463             FOSTAMATINIB     3702       1.0
24   C0549463                PAZOPANIB     3702       1.0
25   C0549463             ZINC ACETATE      325       1.0
26   C0549463              DEQUALINIUM      331       1.0
27   C0549463               EMAPALUMAB     3458       1.0
28   C0549463               OLSALAZINE     3458       1.0
29   C0549463              GLUCOSAMINE     3458       1.0
30   C0549463               IXEKIZUMAB     3605       1.0
31   C0549463              SECUKINUMAB     3605       1.0

In [74]:
df_normal_rare_drug=df_normal_rare_drug.drop_duplicates()

In [75]:
prueba=df_normal_rare_drug.groupby('drug_name').count()

In [76]:
prueba

disease_id  gene_id  jacc_idx
drug_name                                             
DEQUALINIUM                       3        3         3
EMAPALUMAB                        3        3         3
FOSTAMATINIB                      3        3         3
GLUCOSAMINE                       3        3         3
IXEKIZUMAB                        2        2         2
MERCAPTOPURINE                    5        5         5
OLSALAZINE                        3        3         3
PAZOPANIB                         3        3         3
PAZOPANIB HYDROCHLORIDE           3        3         3
SECUKINUMAB                       2        2         2
ZINC ACETATE                      2        2         2

In [77]:
drug=prueba[prueba["disease_id"]>4]

In [78]:
drug

disease_id  gene_id  jacc_idx
drug_name                                    
MERCAPTOPURINE           5        5         5

In [80]:
drug.to_excel("drugs_C0549463_V.xlsx")

In [79]:
df_normal_rare_drug[df_normal_rare_drug["drug_name"]=="MERCAPTOPURINE"]

disease_id       drug_name  gene_id  jacc_idx
0    C0002871  MERCAPTOPURINE     3251       0.0
8    C0003868  MERCAPTOPURINE     3251       0.0
9    C0004135  MERCAPTOPURINE     3251       0.0
10   C0006142  MERCAPTOPURINE     3251       0.0
21   C0549463  MERCAPTOPURINE     3251       1.0

In [81]:
drug_all=df_normal_rare_drug[df_normal_rare_drug["disease_id"]=="C0549463"]

In [82]:
drug_all

disease_id                drug_name  gene_id  jacc_idx
21   C0549463           MERCAPTOPURINE     3251       1.0
22   C0549463  PAZOPANIB HYDROCHLORIDE     3702       1.0
23   C0549463             FOSTAMATINIB     3702       1.0
24   C0549463                PAZOPANIB     3702       1.0
25   C0549463             ZINC ACETATE      325       1.0
26   C0549463              DEQUALINIUM      331       1.0
27   C0549463               EMAPALUMAB     3458       1.0
28   C0549463               OLSALAZINE     3458       1.0
29   C0549463              GLUCOSAMINE     3458       1.0
30   C0549463               IXEKIZUMAB     3605       1.0
31   C0549463              SECUKINUMAB     3605       1.0

In [83]:
drug_all.to_excel("drugs_all_C0549463_v.xlsx")